In [213]:
!pip install datasets transformers[sentencepiece]

In [214]:
!nvidia-smi

Sun Jan 26 12:49:45 2025       
+-----------------------------------------------------------------------------------------+
| NVIDIA-SMI 550.76                 Driver Version: 550.76         CUDA Version: 12.4     |
|-----------------------------------------+------------------------+----------------------+
| GPU  Name                 Persistence-M | Bus-Id          Disp.A | Volatile Uncorr. ECC |
| Fan  Temp   Perf          Pwr:Usage/Cap |           Memory-Usage | GPU-Util  Compute M. |
|                                         |                        |               MIG M. |
|=========================================+========================+======================|
|   0  NVIDIA GeForce RTX 4090        On  |   00000000:E2:00.0 Off |                  Off |
|  0%   31C    P8             19W /  450W |       1MiB /  24564MiB |      0%      Default |
|                                         |                        |                  N/A |
+-----------------------------------------+-----

If you're opening this notebook locally, make sure your environment has an install from the last version of Datasets and a source install of Transformers.

In [215]:
!pip install huggingface_hub

In [216]:
!git config --global credential.helper store

## Getting a corpus

We will need texts to train our tokenizer. We will use the [🤗 Datasets](https://github.com/huggingface/datasets) library to download our text data, which can be easily done with the `load_dataset` function:

In [217]:
from datasets import load_dataset

In [218]:
from huggingface_hub import notebook_login

notebook_login()

In [219]:
dataset = load_dataset("openpecha/deduplication_combined_word_seg_data", name="", split="train")

In [220]:
manual_dataset = dataset.filter(lambda x: x["filename"] == "manual_data.json", num_proc=10)

In [221]:
manual_dataset[0]

{'source': 'ད་ལྟར་བ་ཡོད་ཅི་ཞིག་མེད། །གང་གི་དུས་ཀུན་ཡོད་ཉིད་པ། །དེ་ཡི་མི་རྟག་ཉིད་གང་ལས། ། འདས་པ་ལས་ནི་འདས་གྱུར་པ། །ཅི་ཡི་ཕྱིར་ན་འདས་པར་འགྱུར། ། འདས་པ་ལས་ནི་མ་འདས་པ། །ཅི་ཡི་ཕྱིར་ན་འདས་པར་འགྱུར། །གལ་ཏེ་མ་འོངས་སྐྱེས་ཡོད་ན། །ཇི་ལྟར་ད་ལྟར་བར་མི་འགྱུར། །ཅི་སྟེ་དེ་ལ་སྐྱེ་མེད་ན། །མ་འོངས་རྟག་པར་འགྱུར་རམ་ཅི། ། སྐྱེ་བ་མེད་ཀྱང་འཇིག་པ་ལས། །གལ་ཏེ་མ་འོངས་མི་རྟག་ན། །འདས་ལ་འཇིག་པ་ཡོད་མིན་ཏེ། །དེ་ནི་རྟག་པར་ཅིས་མི་རྟོག། འདས་པ་དང་ནི་ད་ལྟར་བ། །འདི་ནི་མི་རྟག་འགྱུར་མིན་ལ། །',
 'target': 'ད་ལྟར་ བ་ ཡོད་ ཅི་ཞིག་ མེད ། ། གང་ གི་ དུས་ ཀུན་ ཡོད་ ཉིད་པ ། ། དེ་ ཡི་ མི་ རྟག་ ཉིད་ གང་ ལས ། ། འདས་པ་ ལས་ ནི་ འདས་ གྱུར་པ ། ། ཅི་ ཡི་ ཕྱིར་ ན་ འདས་པ ར་ འགྱུར ། ། འདས་པ་ ལས་ ནི་ མ་ འདས་པ ། ། ཅི་ ཡི་ ཕྱིར་ ན་ འདས་པ ར་ འགྱུར ། ། གལ་ཏེ་ མ་འོངས་ སྐྱེས་ ཡོད་ ན ། ། ཇི་ལྟར་ ད་ལྟར་བ ར་མི་ འགྱུར ། ། ཅི་སྟེ་ དེ་ ལ་ སྐྱེ་ མེད་ ན ། ། མ་འོངས་ རྟག་པ ར་ འགྱུར་ རམ་ ཅི ། ། སྐྱེ་བ་ མེད་ ཀྱང་ འཇིག་པ་ ལས ། ། གལ་ཏེ་ མ་འོངས་ མི་ རྟག་ ན ། ། འདས་ ལ་ འཇིག་པ་ ཡོད་ མིན་ ཏེ ། ། དེ་ ནི་ རྟག་པ ར་ ཅི ས་ མི་ རྟོག ། འདས་པ་ དང་ ནི་ ད་ལྟ ར ་བ ། ། འདི་ ནི་ མི་

In [232]:
len(manual_dataset)

20278

In [222]:
remaining_dataset = dataset.filter(lambda x: x["filename"] != "manual_data.json", num_proc=10)

In [223]:
remaining_dataset[9:10]

{'source': ['གཙོ་མོའི་མགྲིན་པར་ཨྃ་དམར་པོ་འབར་བ་ལ་སེམས་གཟུང་༔'],
 'target': ['གཙོ་ མོ འི་ མགྲིན་པ ར་ ཨྃ་ དམར་པོ་ འབར་བ་ ལ་ སེམས་ གཟུང་ ༔'],
 'filename': ['UT3JT13384-005-0028.txt']}

### Unigram model like Albert

Let's now have a look at how we can create a Unigram tokenizer like the one used for training T5. The first step is to create a `Tokenizer` with an empty `Unigram` model:

In [224]:
!pip install tokenizers icecream

In [225]:
from tokenizers import Tokenizer, decoders
from tokenizers.models import Unigram
from tokenizers import pre_tokenizers
from tokenizers.pre_tokenizers import WhitespaceSplit
from tokenizers import trainers
from icecream import ic

tokenizer = Tokenizer(Unigram())

In [ ]:
def batch_iterator(dataset):
    for i in range(0, len(dataset), batch_size):
        yield dataset[i : i + batch_size]["target"]

If we want to have a quick look at how it preprocesses the inputs, we can call the `pre_tokenize_str` method:

In [ ]:
vocab_count=32000
tokenizer.pre_tokenizer = pre_tokenizers.WhitespaceSplit()

In [ ]:
trainer = trainers.UnigramTrainer(vocab_size=vocab_count, special_tokens=["[CLS]", "[SEP]", "<unk>", "<pad>", "[MASK]"], unk_token="<unk>")
tokenizer.train_from_iterator(batch_iterator(manual_dataset), trainer=trainer)

In [ ]:
tokenizer.save(f"./trained_tokenizer_{vocab_count}.json")

In [ ]:
# Load the saved tokenizer
tokenizer = Tokenizer.from_file(f"./trained_tokenizer_{vocab_count}.json")


In [ ]:
cls_token_id = tokenizer.token_to_id("[CLS]")
sep_token_id = tokenizer.token_to_id("[SEP]")

In [226]:
from tokenizers import processors
from tokenizers import Tokenizer, models, processors, decoders

In [234]:
tokenizer.post_processor = processors.TemplateProcessing(
    single="[CLS]:0 $A:0 [SEP]:0",
    pair="[CLS]:0 $A:0 [SEP]:0 $B:1 [SEP]:1",
    special_tokens=[
        ("[CLS]", cls_token_id),
        ("[SEP]", sep_token_id),
    ],
)
tokenizer.decoder = decoders.CTC()

In [235]:
tokenizer_8000 = Tokenizer.from_file(f"./trained_tokenizer_8000.json")
tokenizer_16000 = Tokenizer.from_file(f"./trained_tokenizer_16000.json")
tokenizer_32000 = Tokenizer.from_file(f"./trained_tokenizer_32000.json")

In [236]:
from transformers import AlbertTokenizerFast

tokenizer_8000 = AlbertTokenizerFast(tokenizer_object=tokenizer_8000)
tokenizer_16000 = AlbertTokenizerFast(tokenizer_object=tokenizer_16000)
tokenizer_32000 = AlbertTokenizerFast(tokenizer_object=tokenizer_32000)
##tokenizer_64000 = AlbertTokenizerFast(tokenizer_object=tokenizer_64000)

In [237]:
remaining_dataset[10]

{'source': 'རྨི་ལམ་ཡིན་སྙམ་དུ་བསམ༔',
 'target': 'རྨི་ལམ་ ཡིན་ སྙམ་ དུ་ བསམ ༔',
 'filename': 'UT3JT13384-005-0028.txt'}

In [231]:
for index in range(10, len(remaining_dataset)):
    data = remaining_dataset[index]
    if index == 12:
        break
    ic(data["source"])
    tokenized_data_8000 = tokenizer_8000.tokenize(data["source"])
    ic(tokenized_data_8000)
    tokenized_data_16000 = tokenizer_16000.tokenize(data["source"])
    ic(tokenized_data_16000)
    tokenized_data_32000 = tokenizer_32000.tokenize(data["source"])
    ic(tokenized_data_32000)
    


ic| data["source"]: 'རྨི་ལམ་ཡིན་སྙམ་དུ་བསམ༔'
ic| tokenized_data_8000: ['རྨི་ལམ་', 'ཡིན་', 'སྙམ་', 'དུ་', 'བསམ', '༔']
ic| tokenized_data_16000: ['རྨི་ལམ་', 'ཡིན་', 'སྙམ་', 'དུ་', 'བསམ', '༔']
ic| tokenized_data_32000: ['རྨི་ལམ་', 'ཡིན་', 'སྙམ་', 'དུ་', 'བསམ', '༔']
ic| data["source"]: 'ཉམས་སྐྱེས་པ་ན་རླུང་སེམས་དྲག་ཏུ་གཅུན༔'
ic| tokenized_data_8000: ['ཉམས་', 'སྐྱེས་པ་', 'ན', '་', 'རླུང་', 'སེམས་', 'དྲག་', 'ཏུ་', 'གཅུ', 'ན', '༔']
ic| tokenized_data_16000: ['ཉམས་', 'སྐྱེས་པ་', 'ན', '་', 'རླུང་', 'སེམས་', 'དྲག་', 'ཏུ་', 'གཅུན', '༔']
ic| tokenized_data_32000: ['ཉམས་', 'སྐྱེས་པ་', 'ན', '་', 'རླུང་', 'སེམས་', 'དྲག་', 'ཏུ་', 'གཅུན', '༔']


In [240]:
data = "༸གོང་ས་མཆོག་གི་བོད་དོན་འཐབ་རྩོད་དང་འབྲེལ་བའི་ཕྱག་དེབ་གསར་པ་ཞིག་ཕྱི་ཟླ་གསུམ་པའི་ནང་འདོན་སྤེལ་གནང་རྒྱུ།"
ic(data) 
tokenized_data_8000 = tokenizer_8000.tokenize(data)
ic(tokenized_data_8000)
tokenized_data_16000 = tokenizer_16000.tokenize(data)
ic(tokenized_data_16000)
tokenized_data_32000 = tokenizer_32000.tokenize(data)
ic(tokenized_data_32000)
ic(tokenizer_8000.encode(data))

ic| data: '༸གོང་ས་མཆོག་གི་བོད་དོན་འཐབ་རྩོད་དང་འབྲེལ་བའི་ཕྱག་དེབ་གསར་པ་ཞིག་ཕྱི་ཟླ་གསུམ་པའི་ནང་འདོན་སྤེལ་གནང་རྒྱུ།'
ic| tokenized_data_8000: ['༸གོང་ས་',
                          'མཆོག་',
                          'གི་',
                          'བོད་',
                          'དོན་',
                          'འཐབ་རྩོད་',
                          'དང་',
                          'འབྲེལ་བ',
                          'འི་',
                          'ཕྱག་',
                          'དེབ་',
                          'གསར་པ་',
                          'ཞིག་',
                          'ཕྱི་',
                          'ཟླ་',
                          'གསུམ་པ',
                          'འི་',
                          'ནང་',
                          'འདོན་',
                          'སྤེལ་',
                          'གནང་',
                          'རྒྱུ',
                          '།']
ic| tokenized_data_16000: ['༸གོང་ས་',
                           'མཆོག་',
                     

[0,
 2163,
 152,
 25,
 201,
 47,
 3426,
 9,
 662,
 7,
 267,
 1522,
 2426,
 59,
 256,
 636,
 348,
 7,
 85,
 1067,
 1238,
 717,
 246,
 5,
 1]

In [152]:
tokenized_data

['སྣང་', 'གསུམ་', 'དབྱིངས་', 'སུ་', 'ཐིམ་པ', '་', 'ལས', '༔']

In [166]:
tokenized_data_16000

['སྣང་', 'གསུམ་', 'དབྱིངས་', 'སུ་', 'ཐིམ་པ', '་', 'ལས', '༔']

In [ ]:
tokenized_data_32000

## Use your new tokenizer to train a language model!

You can either use your new tokenizer in the language modeling from scratch notebook [Link to come] or use the `--tokenizer_name` argument in the [language modeling scripts](https://github.com/huggingface/transformers/tree/master/examples/pytorch/language-modeling) to use it there to train a model from scratch.

In [241]:
notebook_login()


In [253]:
from huggingface_hub import login, create_repo, Repository

repo_name = "ta4tsering/NLP-Unigram_language_model_tokenizer"
repo_url = create_repo(repo_name, repo_type="model", private=False)
print(f"Repository created: {repo_url}")

HfHubHTTPError: 409 Client Error: Conflict for url: https://huggingface.co/api/repos/create (Request ID: Root=1-6796358c-51a27b1e2f84e1b55e1c5564;b3b3b6a1-c6c3-443d-a173-3b62474886bf)

You already created this model repo

In [248]:
!pip install --upgrade huggingface_hub

In [256]:
repo_path = "/home"
repo = Repository(local_dir=repo_path, clone_from=repo_url)

/opt/conda/lib/python3.10/site-packages/huggingface_hub/utils/_deprecation.py:131: FutureWarning: 'Repository' (from 'huggingface_hub.repository') is deprecated and will be removed from version '1.0'. Please prefer the http-based alternatives instead. Given its large adoption in legacy code, the complete removal is only planned on next major release.
For more details, please read https://huggingface.co/docs/huggingface_hub/concepts/git_vs_http.
  warnings.warn(warning_message, FutureWarning)


OSError: Looks like you do not have git-lfs installed, please install. You can install from https://git-lfs.github.com/. Then run `git lfs install` (you only have to do this once).

In [ ]:
import os
from huggingface_hub import upload_file

# Define the local folder and repo_id
folder_path = "/home/NLP-Unigram_language_model_tokenizer/"  # Local folder path (should match your repo_id)
repo_id = "ta4tsering/NLP-Unigram_language_model_tokenizer"  # Replace with your Hugging Face repo ID

# Iterate through all files in the folder
for root, _, files in os.walk(folder_path):
    for file_name in files:
        local_file_path = os.path.join(root, file_name)
        repo_file_path = os.path.relpath(local_file_path, folder_path)  # Keep folder structure

        # Upload file to the repo
        upload_file(
            path_or_fileobj=local_file_path,
            path_in_repo=repo_file_path,
            repo_id=repo_id,
            repo_type="model",
            commit_message=f"Add {repo_file_path}",
        )
        print(f"Uploaded {repo_file_path}")


In [257]:
!git lfs install

git: 'lfs' is not a git command. See 'git --help'.

The most similar command is
	log


In [ ]:
repo.push_to_hub(commit_message="Initial commit")
print("Files pushed to Hugging Face!")